# Predict tags on StackOverflow with linear models

In this assignment you will learn how to predict tags for posts from [StackOverflow](https://stackoverflow.com). To solve this task you will use multilabel classification approach.

### Libraries

In this task you will need the following libraries:
- [Numpy](http://www.numpy.org) — a package for scientific computing.
- [Pandas](https://pandas.pydata.org) — a library providing high-performance, easy-to-use data structures and data analysis tools for the Python
- [scikit-learn](http://scikit-learn.org/stable/index.html) — a tool for data mining and data analysis.
- [NLTK](http://www.nltk.org) — a platform to work with natural language.

### Data

The following cell will download all data required for this assignment into the folder `week1/data`.

In [6]:
import sys
sys.path.append("..")
from common.download_utils import download_week1_resources

download_week1_resources()

ImportError: No module named 'common'

### Grading
We will create a grader instance below and use it to collect your answers. Note that these outputs will be stored locally inside grader and will be uploaded to platform only after running submitting function in the last part of this assignment. If you want to make partial submission, you can run that cell any time you want.

In [7]:
from grader import Grader

ImportError: No module named 'grader'

In [5]:
grader = Grader()

### Text preprocessing

For this and most of the following assignments you will need to use a list of stop words. It can be downloaded from *nltk*:

In [6]:
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In this task you will deal with a dataset of post titles from StackOverflow. You are provided a split to 3 sets: *train*, *validation* and *test*. All corpora (except for *test*) contain titles of the posts and corresponding tags (100 tags are available). The *test* set is provided for Coursera's grading and doesn't contain answers. Upload the corpora using *pandas* and look at the data:

In [7]:
from ast import literal_eval
import pandas as pd
import numpy as np

In [8]:
def read_data(filename):
    data = pd.read_csv(filename, sep='\t')
    data['tags'] = data['tags'].apply(literal_eval)
    return data

In [9]:
train = read_data('data/train.tsv')
validation = read_data('data/validation.tsv')
test = pd.read_csv('data/test.tsv', sep='\t')

In [10]:
train.head()

title                  tags
0                How to draw a stacked dotplot in R?                   [r]
1  mysql select all records where a datetime fiel...          [php, mysql]
2             How to terminate windows phone 8.1 app                  [c#]
3  get current time in a specific country via jquery  [javascript, jquery]
4                      Configuring Tomcat to Use SSL                [java]

As you can see, *title* column contains titles of the posts and *tags* column contains the tags. It could be noticed that a number of tags for a post is not fixed and could be as many as necessary.

For a more comfortable usage, initialize *X_train*, *X_val*, *X_test*, *y_train*, *y_val*.

In [11]:
X_train, y_train = train['title'].values, train['tags'].values
X_val, y_val = validation['title'].values, validation['tags'].values
X_test = test['title'].values

One of the most known difficulties when working with natural data is that it's unstructured. For example, if you use it "as is" and extract tokens just by splitting the titles by whitespaces, you will see that there are many "weird" tokens like *3.5?*, *"Flip*, etc. To prevent the problems, it's usually useful to prepare the data somehow. In this task you'll write a function, which will be also used in the other assignments. 

**Task 1 (TextPrepare).** Implement the function *text_prepare* following the instructions. After that, run the function *test_test_prepare* to test it on tiny cases and submit it to Coursera.

In [12]:
import re

In [22]:
REPLACE_BY_SPACE_RE = re.compile('[/(){}\[\]\|@,;]')
BAD_SYMBOLS_RE = re.compile('[^0-9a-z #+_]')
STOPWORDS = set(stopwords.words('english'))

def text_prepare(text):
    """
        text: a string
        
        return: modified initial string
    """
    text = text.lower() # lowercase text
    text = re.sub('[/(){}\[\]\|@,;]',' ', text)# replace REPLACE_BY_SPACE_RE symbols by space in text
    text = re.sub('[^0-9a-z #+_]','', text)# delete symbols which are in BAD_SYMBOLS_RE from text
    text = ' '.join([x for x in text.split() if x not in STOPWORDS])# delete stopwords from text
#     print(text)
    return text

In [23]:
def test_text_prepare():
    examples = ["SQL Server - any equivalent of Excel's CHOOSE function?",
                "How to free c++ memory vector<int> * arr?"]
    answers = ["sql server equivalent excels choose function", 
               "free c++ memory vectorint arr"]
    for ex, ans in zip(examples, answers):
        if text_prepare(ex) != ans:
            return "Wrong answer for the case: '%s'" % ex
    return 'Basic tests are passed.'

In [24]:
print(test_text_prepare())

sql server equivalent excels choose function
free c++ memory vectorint arr
Basic tests are passed.


Run your implementation for questions from file *text_prepare_tests.tsv* to earn the points.

In [25]:
prepared_questions = []
for line in open('data/text_prepare_tests.tsv', encoding='utf-8'):
    line = text_prepare(line.strip())
    prepared_questions.append(line)
text_prepare_results = '\n'.join(prepared_questions)

grader.submit_tag('TextPrepare', text_prepare_results)

sqlite php readonly
creating multiple textboxes dynamically
self one prefer javascript
save php date string mysql database timestamp
fill dropdownlist data xml file aspnet application
programmatically trigger jqueryui draggables drag event
get value method argument via reflection java
knockout mapingfromjs observablearray json object data gets lost
facebook connect localhost weird stuff
fullcalendar prev next click
syntaxerror unexpected token
effective way float double comparison
gem install rails fails dns error
listshuttle component richfaces getting updated
laravel responsedownload show images laravel
wrong rspec test
calendar display using java swing
python selenium import regular firefox profile addons
random number 2 variables values
altering http responses firefox extension
start session python web application
align radio buttons horizontally django forms
count number rows sqlite database
wordpress wp_rewrite rules
removing sheet excel 2005 using php
php fatal error function na

Now we can preprocess the titles using function *text_prepare* and  making sure that the headers don't have bad symbols:

In [28]:
X_train = [text_prepare(x) for x in X_train]
X_val = [text_prepare(x) for x in X_val]
X_test = [text_prepare(x) for x in X_test]

draw stacked dotplot r
mysql select records datetime field less specified value
terminate windows phone 81 app
get current time specific country via jquery
configuring tomcat use ssl
awesome nested set plugin add new children tree various levels
create map json response ruby rails 3
rspec test method called
springboot catalina lifecycle exception
import data excel mysql database using php
obtaining object javalangclasst object parameterized type without constructing class q_uestion
ipad selecting text inside text input tap
jquerys function object
eclipse c++ mingw lauch program terminated
javascript call one prototype method another prototype method
get intersection list sets
longer able hide keyboard viewwilldisappear ios7
fetch key json swift
change pivot header template windows phone 8
connectionstring encryption
let ui refresh long running ui operation
better way execute ruby file using python get ruby console output ruby file run python
make 2 thumbnails codeigniter
java character

double accuracy
run msi installer cmd admin using c#
xcode 7x crashes editing storyboards
infinite looping switch case given wrong input
makefile php scripts
load previous page submitting form php
parallel mapping functions ipython w multiple parameters
difference afxbeginthread createthread
bring bootstrap 3 panels bootstrap 2 website
try catch help end statement expected
php dollar amount regular expression
confusion redirect_uri oauth 20
reading xml file iphone
apply css javascript dropbox folder using blogger
constructor threw exception nested exception javalangnoclassdeffounderror javax servlet servletcontext
creating shortcut file java
django best practice number model classes per file directory structure
enable gd library php 7 linux ubuntu
cannot clear textbox keypress event
deallocation memory allocated stdstring c++
write get method repository pattern
comparing two arraylists java
rotate panel winform
writing reading repeated extended fields protobuf
comparing python lists
op

resetting static variable beginning mstest test method
redirecting user page login
error validator could found type javalanginteger
subtract year datetime
correct way setting role user registered identity
best practise using directorygetfiles enumeratefiles target directory contains locked files
initialize c# static class actually needed
php script stuck exec even running command backgroud windows
java tomcat memory leak redhat linux
mockito cannot instantiate injectmocks
save video stream socket file
c# dynamic resolves internal properties methods
python print message warnings
heroku app doesnt work create heroku cli
underline textblock mouseenter
limitation use windows azure mobile android service start boot
wait task finished c#
getting wrong c runtime version manifest files visual studio 2008
returning liststring json call jquery undefined length
orghibernatequeryexception named parameters set
auto login within iframe
error initializing cropperjs
php unserialize current object
what

smtpclient operation timed
setup multiple language yii2 simple way
python comma print
java conversation 2 threads piped input output streams
rails factory girl getting email already taken
convert sslsocket python code ruby
creating twodimensional array
simple question c copying variables user defined struct type
get project specific jira issues using jira rest api net
load data scrolling horizontally div overflow
styling reacttoolboxs button working
mvvm grouping items listview
linqtosql member defining identity object cannot changed
linq contains syntax issue
retrive data database show jlabel netbeans
error generating jasperreport development mode
check directory path ends directory_separator
javascript es6 class definition accessible window global
exc_bad_access error trying create object class xcode
javascript appending children element
using float nan represent missing values safe
get return value taskwaitall console app
django rest framework serializing deserializing list primitiv

change custom logo link wordpress
slow sqlcommand performance longer commandtext
convert character string date date class day value missing
c++ overloading assignment operator
parse iframe using lxml
make html scrollbar start bottom
show additional details section magento product page description
prettify json curl osx
class without property called type get orghibernatepropertynotfoundexception could find setter property type class
parsing xml tags php
issue positioning skspritenode skscene
get response form post
create constant python
ruby mri 187 file writing thread safety
parsing user input console commandline arguments c#
map onetomany relationship using c# code mapping
lockbits stride 1bpp indexed image byte boundaries
aspnet mvc unity dependency injection gives exception trying resolve controller
extjs layout extension causing error extalljs
private static functions javascript
check scrollbars present javascript
convert float plain string representation
updating database automati

...

way disable tab input typetext
spring security 4 preauthorize hasrole working
access mp3 music data using python
provider field connection string oledb
create jsonarray without key value
validate jtextfield
disable alt + shift + tab using c#
adding urls api keys environment variable ruby
undefined error using data attribute jquery
query mongodb embedded document via c# driver
make uipickerview show uitableviewcell swift
break large csv data file individual data files using r
set div tag height width using javascript
access maven artifact pom using mavens java api
generating matplotlib graphs without running x server
sending key value array ajax
pass ref parameter inside lambda express thread issue
populate form iframe external website
allowing user select certain amount checkboxes
jackson slow
issue jstl foreach iterate arraylist
r plot make histogram horizontal lines using plot
c# display binding data datagridviewcomboboxcolumn datagridview
angular scopeon destroy
error occured proces

create folder javascript
copy uitextfield data uilabel
good open source web crawling framework c#
net c# anonymous pipes misunderstood
php forms valuephp_post total_amount vs value_post total_amount
check class name using javascript
complexity setinsert
sum values python list dictionaries using common key value
tkinter display windows
unable set selected value easydropdownjs
javascript local variable works like class variable window
reload browser page click back button
could send data server client via websocket
convert string datetime node js
possible compress base64 png string
uitableviewcell reorganize subviews delete button appears
select records n child records
display germany umlauts sql php
understanding behavior pythons set
nunit example code
run javascript function background without freezing ui
magento creating new instances helper class time loop runs
ajax multiple drop list
multiple managed beans
unable use xbuild build solution mono
efficient file reading c++11 14
tofixed

sending activation emailsdjango
rxjava reduce unsafe parallelized
datepicker double selecteddatechanged event typing date
c++ preprocessor variable
redirect json response one php page another
regex javascript transform degrees decimal minutes decimal degrees
pdo php fetch class
div center using classcenterblock bootstrap
nodejs cannot read property undefined
problem short date format php
execute imagemagick php
sum values one mysql column group values column using php foreach
spring stringtrimmereditor working
data getting saved database
python 3 counting matches two lists including duplicates
draw line realtime measurement fabricjs
jpa saving list values comma separated values
best practice multiple longmethods using backgroundworker
simulate multiple user input junit
urisyntaxexception illegal character query
adjust number rows form textarea laravel 5
curl append resource id #2 output
struts2 + hibernate3 + jasperreport 50 getting blank report
way handle variable number parameters te

amazon web services java classpath
c pointers arrays copying contents another array
cancel onclick javascript functions another javascript
c# asychronous sockets multithreading using async sockets threading correctly
touch updated_at column rails 232
wordpress tinymce issue article posting
angular update scope event
run php script cron
turn push notification function swift
lambdas event handlers
image referencing css wicket
sorting collection hashsets
c# xml deserialize array element values
java scanner multiple delimiters
best shortest books c++ stl c# j2se prepare job inteview tests
get index key python dictionary
upgrade php curl version 7360
c++ fill vector another vector
getting entire output subprocesspopen
ruby caseinsensitive array comparison
finding golden ratio accurately till 20 decimal places
getting ip specific url
mac app storyboard access document nsviewcontroller
extend error runtimeexception creating custom unchecked exception
window load wrapper jquery
source availabl

beautifulsoup findall class attribute unicode encode error
devexpress set cell value unhandled exception type systemstackoverflowexception occurred mscorlibdll
safe qt qqueuedequeue c++ inline pointer dereference
replacing rgb values numpy array integer extremely slow
rstudio twitter handshake giving error unauthorized via twitterr
php regex match word group words capital letters
real time ajax comments
jquery change background image gradually scrolling
g1 young gc free memory tospace exhausted
got stuck using prepare bindvalue c++ qt
binding working custom user controls dependency property
outlook shows html text
change file name assemblynameexeconfig appconfig output directory visual studio
asynchronous take blocking collection
audio recording error kaudioqueueerr_cannotstart iphone os 30
get weekdays php
write rangebased forloop argv
cellforitematindexpath called numberofitemsinsection
lightblue python module working mac
draw simple line chart google chart json data dates x axis
mak

In [29]:
X_train[:3]

['draw stacked dotplot r',
 'mysql select records datetime field less specified value',
 'terminate windows phone 81 app']

For each tag and for each word calculate how many times they occur in the train corpus. 

**Task 2 (WordsTagsCount).** Find 3 most popular tags and 3 most popular words in the train data and submit the results to earn the points.

In [75]:
import operator
# Dictionary of all tags from train corpus with their counts.
tags_counts = {}

for x1 in X_val:
    for x in x1.split():
        if x in tags_counts:
            tags_counts[x]+=1
        else:
            tags_counts[x]=1
# Dictionary of all words from train corpus with their counts.
words_counts = {}
for x in X_train:
    y=x.split()
    for j in y:
        if j in words_counts:
            words_counts[j]+=1
        else:
            words_counts[j]=1

sorted_x = sorted(tags_counts.items(), key=operator.itemgetter(1), reverse=True)[:3]
# finalString = ','.join(sorted_x)
finalString =sorted_x[0][0]+','+sorted_x[1][0]+','+sorted_x[2][0]
# print(finalString)
sorted_words = sorted(words_counts.items(), key=operator.itemgetter(1))
finalString = finalString+'\n'+sorted_words[len(sorted_words)-1][0]+','+sorted_words[len(sorted_words)-2][0]+','+sorted_words[len(sorted_words)-3][0]
print(finalString)


using,php,java
using,php,java


We are assuming that *tags_counts* and *words_counts* are dictionaries like `{'some_word_or_tag': frequency}`. After applying the sorting procedure, results will be look like this: `[('most_popular_word_or_tag', frequency), ('less_popular_word_or_tag', frequency), ...]`. The grader gets the results in the following format (two comma-separated strings with line break):

    tag1,tag2,tag3
    word1,word2,word3

Pay attention that in this assignment you should not submit frequencies or some additional information.

In [76]:
most_common_tags = sorted(tags_counts.items(), key=lambda x: x[1], reverse=True)[:3]
most_common_words = sorted(words_counts.items(), key=lambda x: x[1], reverse=True)[:3]

grader.submit_tag('WordsTagsCount', '%s\n%s' % (','.join(tag for tag, _ in most_common_tags), 
                                                ','.join(word for word, _ in most_common_words)))

Current answer for task WordsTagsCount is:
 using,php,java
using,php,java...


### Transforming text to a vector

Machine Learning algorithms work with numeric data and we cannot use the provided text data "as is". There are many ways to transform text data to numeric vectors. In this task you will try to use two of them.

#### Bag of words

One of the well-known approaches is a *bag-of-words* representation. To create this transformation, follow the steps:
1. Find *N* most popular words in train corpus and numerate them. Now we have a dictionary of the most popular words.
2. For each title in the corpora create a zero vector with the dimension equals to *N*.
3. For each text in the corpora iterate over words which are in the dictionary and increase by 1 the corresponding coordinate.

Let's try to do it for a toy example. Imagine that we have *N* = 4 and the list of the most popular words is 

    ['hi', 'you', 'me', 'are']

Then we need to numerate them, for example, like this: 

    {'hi': 0, 'you': 1, 'me': 2, 'are': 3}

And we have the text, which we want to transform to the vector:

    'hi how are you'

For this text we create a corresponding zero vector 

    [0, 0, 0, 0]
    
And iterate over all words, and if the word is in the dictionary, we increase the value of the corresponding position in the vector:

    'hi':  [1, 0, 0, 0]
    'how': [1, 0, 0, 0] # word 'how' is not in our dictionary
    'are': [1, 0, 0, 1]
    'you': [1, 1, 0, 1]

The resulting vector will be 

    [1, 1, 0, 1]
   
Implement the described encoding in the function *my_bag_of_words* with the size of the dictionary equals to 5000. To find the most common words use train data. You can test your code using the function *test_my_bag_of_words*.

In [3]:
import operator
DICT_SIZE = 5000
selected_words = sorted(words_counts, key = operator.itemgetter(),reverse = True)[:5000]
WORDS_TO_INDEX = {}####### YOUR CODE HERE #######
INDEX_TO_WORDS = {}####### YOUR CODE HERE #######
for i in range(0,5000):
    WORDS_TO_INDEX[selected_words[i][0]]=i
    INDEX_TO_WORDS[i]=selected_words[i][0]
ALL_WORDS = WORDS_TO_INDEX.keys()

def my_bag_of_words(text, words_to_index, dict_size):
    """
        text: a string
        dict_size: size of the dictionary
        
        return a vector which is a bag-of-words representation of 'text'
    """
    result_vector = np.zeros(dict_size)
    text_split = text.split()
    for i in range(0,len(text_split)):
        if text_split[i] in words_to_index.keys():
            result_vctor[words_to_index[text_split[i]]]+=1

    ######################################
    ######### YOUR CODE HERE #############
    ######################################
    return result_vector

NameError: name 'words_counts' is not defined

In [79]:
def test_my_bag_of_words():
    words_to_index = {'hi': 0, 'you': 1, 'me': 2, 'are': 3}
    examples = ['hi how are you']
    answers = [[1, 1, 0, 1]]
    for ex, ans in zip(examples, answers):
        if (my_bag_of_words(ex, words_to_index, 4) != ans).any():
            return "Wrong answer for the case: '%s'" % ex
    return 'Basic tests are passed.'

In [80]:
print(test_my_bag_of_words())

NameError: name 'my_bag_of_words' is not defined

Now apply the implemented function to all samples (this might take up to a minute):

In [ ]:
from scipy import sparse as sp_sparse

In [ ]:
X_train_mybag = sp_sparse.vstack([sp_sparse.csr_matrix(my_bag_of_words(text, WORDS_TO_INDEX, DICT_SIZE)) for text in X_train])
X_val_mybag = sp_sparse.vstack([sp_sparse.csr_matrix(my_bag_of_words(text, WORDS_TO_INDEX, DICT_SIZE)) for text in X_val])
X_test_mybag = sp_sparse.vstack([sp_sparse.csr_matrix(my_bag_of_words(text, WORDS_TO_INDEX, DICT_SIZE)) for text in X_test])
print('X_train shape ', X_train_mybag.shape)
print('X_val shape ', X_val_mybag.shape)
print('X_test shape ', X_test_mybag.shape)

As you might notice, we transform the data to sparse representation, to store the useful information efficiently. There are many [types](https://docs.scipy.org/doc/scipy/reference/sparse.html) of such representations, however sklearn algorithms can work only with [csr](https://docs.scipy.org/doc/scipy/reference/generated/scipy.sparse.csr_matrix.html#scipy.sparse.csr_matrix) matrix, so we will use this one.

**Task 3 (BagOfWords).** For the 11th row in *X_train_mybag* find how many non-zero elements it has. In this task the answer (variable *non_zero_elements_count*) should be a number, e.g. 20.

In [ ]:
row = X_train_mybag[10].toarray()[0]
non_zero_elements_count = ####### YOUR CODE HERE #######

grader.submit_tag('BagOfWords', str(non_zero_elements_count))

#### TF-IDF

The second approach extends the bag-of-words framework by taking into account total frequencies of words in the corpora. It helps to penalize too frequent words and provide better features space. 

Implement function *tfidf_features* using class [TfidfVectorizer](http://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.TfidfVectorizer.html) from *scikit-learn*. Use *train* corpus to train a vectorizer. Don't forget to take a look into the arguments that you can pass to it. We suggest that you filter out too rare words (occur less than in 5 titles) and too frequent words (occur more than in 90% of the titles). Also, use bigrams along with unigrams in your vocabulary. 

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [ ]:
def tfidf_features(X_train, X_val, X_test):
    """
        X_train, X_val, X_test — samples        
        return TF-IDF vectorized representation of each sample and vocabulary
    """
    # Create TF-IDF vectorizer with a proper parameters choice
    # Fit the vectorizer on the train set
    # Transform the train, test, and val sets and return the result
    
    
    tfidf_vectorizer = ####### YOUR CODE HERE #######
    
    ######################################
    ######### YOUR CODE HERE #############
    ######################################
    
    return X_train, X_val, X_test, tfidf_vectorizer.vocabulary_

Once you have done text preprocessing, always have a look at the results. Be very careful at this step, because the performance of future models will drastically depend on it. 

In this case, check whether you have c++ or c# in your vocabulary, as they are obviously important tokens in our tags prediction task:

In [ ]:
X_train_tfidf, X_val_tfidf, X_test_tfidf, tfidf_vocab = tfidf_features(X_train, X_val, X_test)
tfidf_reversed_vocab = {i:word for word,i in tfidf_vocab.items()}

In [ ]:
######### YOUR CODE HERE #############

If you can't find it, we need to understand how did it happen that we lost them? It happened during the built-in tokenization of TfidfVectorizer. Luckily, we can influence on this process. Get back to the function above and use '(\S+)' regexp as a *token_pattern* in the constructor of the vectorizer.  

Now, use this transormation for the data and check again.

In [ ]:
######### YOUR CODE HERE #############

### MultiLabel classifier

As we have noticed before, in this task each example can have multiple tags. To deal with such kind of prediction, we need to transform labels in a binary form and the prediction will be a mask of 0s and 1s. For this purpose it is convenient to use [MultiLabelBinarizer](http://scikit-learn.org/stable/modules/generated/sklearn.preprocessing.MultiLabelBinarizer.html) from *sklearn*.

In [ ]:
from sklearn.preprocessing import MultiLabelBinarizer

In [ ]:
mlb = MultiLabelBinarizer(classes=sorted(tags_counts.keys()))
y_train = mlb.fit_transform(y_train)
y_val = mlb.fit_transform(y_val)

Implement the function *train_classifier* for training a classifier. In this task we suggest to use One-vs-Rest approach, which is implemented in [OneVsRestClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multiclass.OneVsRestClassifier.html) class. In this approach *k* classifiers (= number of tags) are trained. As a basic classifier, use [LogisticRegression](http://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html). It is one of the simplest methods, but often it performs good enough in text classification tasks. It might take some time, because a number of classifiers to train is large.

In [ ]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.linear_model import LogisticRegression, RidgeClassifier

In [ ]:
def train_classifier(X_train, y_train):
    """
      X_train, y_train — training data
      
      return: trained classifier
    """
    
    # Create and fit LogisticRegression wraped into OneVsRestClassifier.

    ######################################
    ######### YOUR CODE HERE #############
    ######################################    

Train the classifiers for different data transformations: *bag-of-words* and *tf-idf*.

In [ ]:
classifier_mybag = train_classifier(X_train_mybag, y_train)
classifier_tfidf = train_classifier(X_train_tfidf, y_train)

Now you can create predictions for the data. You will need two types of predictions: labels and scores.

In [ ]:
y_val_predicted_labels_mybag = classifier_mybag.predict(X_val_mybag)
y_val_predicted_scores_mybag = classifier_mybag.decision_function(X_val_mybag)

y_val_predicted_labels_tfidf = classifier_tfidf.predict(X_val_tfidf)
y_val_predicted_scores_tfidf = classifier_tfidf.decision_function(X_val_tfidf)

Now take a look at how classifier, which uses TF-IDF, works for a few examples:

In [ ]:
y_val_pred_inversed = mlb.inverse_transform(y_val_predicted_labels_tfidf)
y_val_inversed = mlb.inverse_transform(y_val)
for i in range(3):
    print('Title:\t{}\nTrue labels:\t{}\nPredicted labels:\t{}\n\n'.format(
        X_val[i],
        ','.join(y_val_inversed[i]),
        ','.join(y_val_pred_inversed[i])
    ))

Now, we would need to compare the results of different predictions, e.g. to see whether TF-IDF transformation helps or to try different regularization techniques in logistic regression. For all these experiments, we need to setup evaluation procedure. 

### Evaluation

To evaluate the results we will use several classification metrics:
 - [Accuracy](http://scikit-learn.org/stable/modules/generated/sklearn.metrics.accuracy_score.html)
 - [F1-score](http://scikit-learn.org/stable/modules/generated/sklearn.metrics.f1_score.html)
 - [Area under ROC-curve](http://scikit-learn.org/stable/modules/generated/sklearn.metrics.roc_auc_score.html)
 - [Area under precision-recall curve](http://scikit-learn.org/stable/modules/generated/sklearn.metrics.average_precision_score.html#sklearn.metrics.average_precision_score) 
 
Make sure you are familiar with all of them. How would you expect the things work for the multi-label scenario? Read about micro/macro/weighted averaging following the sklearn links provided above.

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from sklearn.metrics import roc_auc_score 
from sklearn.metrics import average_precision_score
from sklearn.metrics import recall_score

Implement the function *print_evaluation_scores* which calculates and prints to stdout:
 - *accuracy*
 - *F1-score macro/micro/weighted*
 - *Precision macro/micro/weighted*

In [ ]:
def print_evaluation_scores(y_val, predicted):
    
    ######################################
    ######### YOUR CODE HERE #############
    ######################################

In [ ]:
print('Bag-of-words')
print_evaluation_scores(y_val, y_val_predicted_labels_mybag)
print('Tfidf')
print_evaluation_scores(y_val, y_val_predicted_labels_tfidf)

You might also want to plot some generalization of the [ROC curve](http://scikit-learn.org/stable/modules/model_evaluation.html#receiver-operating-characteristic-roc) for the case of multi-label classification. Provided function *roc_auc* can make it for you. The input parameters of this function are:
 - true labels
 - decision functions scores
 - number of classes

In [ ]:
from metrics import roc_auc
%matplotlib inline

In [ ]:
n_classes = len(tags_counts)
roc_auc(y_val, y_val_predicted_scores_mybag, n_classes)

In [ ]:
n_classes = len(tags_counts)
roc_auc(y_val, y_val_predicted_scores_tfidf, n_classes)

**Task 4 (MultilabelClassification).** Once we have the evaluation set up, we suggest that you experiment a bit with training your classifiers. We will use *F1-score weighted* as an evaluation metric. Our recommendation:
- compare the quality of the bag-of-words and TF-IDF approaches and chose one of them.
- for the chosen one, try *L1* and *L2*-regularization techniques in Logistic Regression with different coefficients (e.g. C equal to 0.1, 1, 10, 100).

You also could try other improvements of the preprocessing / model, if you want. 

In [ ]:
######################################
######### YOUR CODE HERE #############
######################################

When you are happy with the quality, create predictions for *test* set, which you will submit to Coursera.

In [ ]:
test_predictions = ######### YOUR CODE HERE #############
test_pred_inversed = mlb.inverse_transform(test_predictions)

test_predictions_for_submission = '\n'.join('%i\t%s' % (i, ','.join(row)) for i, row in enumerate(test_pred_inversed))
grader.submit_tag('MultilabelClassification', test_predictions_for_submission)

### Analysis of the most important features

Finally, it is usually a good idea to look at the features (words or n-grams) that are used with the largest weigths in your logistic regression model.

Implement the function *print_words_for_tag* to find them. Get back to sklearn documentation on [OneVsRestClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multiclass.OneVsRestClassifier.html) and [LogisticRegression](http://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html) if needed.

In [ ]:
def print_words_for_tag(classifier, tag, tags_classes, index_to_words, all_words):
    """
        classifier: trained classifier
        tag: particular tag
        tags_classes: a list of classes names from MultiLabelBinarizer
        index_to_words: index_to_words transformation
        all_words: all words in the dictionary
        
        return nothing, just print top 5 positive and top 5 negative words for current tag
    """
    print('Tag:\t{}'.format(tag))
    
    # Extract an estimator from the classifier for the given tag.
    # Extract feature coefficients from the estimator. 
    
    ######################################
    ######### YOUR CODE HERE #############
    ######################################
    
    top_positive_words = # top-5 words sorted by the coefficiens.
    top_negative_words = # bottom-5 words  sorted by the coefficients.
    print('Top positive words:\t{}'.format(', '.join(top_positive_words)))
    print('Top negative words:\t{}\n'.format(', '.join(top_negative_words)))

In [ ]:
print_words_for_tag(classifier_tfidf, 'c', mlb.classes, tfidf_reversed_vocab, ALL_WORDS)
print_words_for_tag(classifier_tfidf, 'c++', mlb.classes, tfidf_reversed_vocab, ALL_WORDS)
print_words_for_tag(classifier_tfidf, 'linux', mlb.classes, tfidf_reversed_vocab, ALL_WORDS)

### Authorization & Submission
To submit assignment parts to Cousera platform, please, enter your e-mail and token into variables below. You can generate token on this programming assignment page. <b>Note:</b> Token expires 30 minutes after generation.

In [ ]:
grader.status()

In [ ]:
STUDENT_EMAIL = # EMAIL 
STUDENT_TOKEN = # TOKEN 
grader.status()

If you want to submit these answers, run cell below

In [ ]:
grader.submit(STUDENT_EMAIL, STUDENT_TOKEN)